In [ ]:
import datetime
import pandas as pd
import numpy as np

from graphics import plot_time_color_map, plot_color_map
from analytics import Swaption, BlackSwaption, BlackSwaptionVolSurface, Index, Portfolio
from analytics.scenarios import run_swaption_scenarios, run_index_scenarios, run_portfolio_scenarios
from scipy.interpolate import SmoothBivariateSpline
from db import dbengine

In [ ]:
#Delta Chart: Red = Long Risk, Blue = Short Risk

In [ ]:
def plot_trade_scenarios(portf, shock_min=-.15, shock_max=.2, period=-1, vol_time_roll=True):
    portf.reset_pv()
    earliest_date = min(portf.swaptions, key=lambda x: x.exercise_date).exercise_date
    date_range = pd.bdate_range(portf.indices[0].value_date,
                                earliest_date - pd.tseries.offsets.BDay(), freq='3B')
    vol_shock = np.arange(-0.15, 0.3, 0.01)
    spread_shock = np.arange(shock_min, shock_max, 0.01)
    index = portf.indices[0].name.split()[1]
    series = portf.indices[0].name.split()[3][1:]
    vs = BlackSwaptionVolSurface(index, series, value_date=portf.indices[0].value_date)
    vol_surface = vs[vs.list(option_type='payer')[-1]]

    df = run_portfolio_scenarios(portf, date_range, spread_shock, vol_shock, vol_surface,
                                 params=["pnl","delta"])

    hy_plot_range = 100 + (500 - portf.indices[0].spread * (1 + spread_shock)) * \
                    abs(portf.indices[0].DV01) / portf.indices[0].notional * 100

    shock =  hy_plot_range if index == 'HY' else portf.indices[0].spread * (1 + spread_shock)

    plot_time_color_map(df[round(df.vol_shock,2)==0], shock, 'pnl', index=index)
    plot_time_color_map(df[round(df.vol_shock,2)==.2], shock, 'pnl', index=index)
    plot_color_map(df.loc[date_range[period]], shock, vol_shock, 'pnl', index=index)

In [ ]:
#Ad hoc
option_delta = Index.from_name('IG', 30, '5yr', value_date=datetime.date(2018, 5, 17))
option_delta.spread = 61
option1 = BlackSwaption(option_delta, datetime.date(2018, 8, 15), 60, option_type="payer")
option2 = BlackSwaption(option_delta, datetime.date(2018, 8, 15), 80, option_type="payer")
option3 = BlackSwaption(option_delta, datetime.date(2018, 8, 15), 80, option_type="payer")
option1.sigma = .381
option2.sigma = .545
option3.sigma = .69
option1.notional = 100_000_000
option2.notional = 300_000_000
option3.notional = 1
option1.direction = 'Long'
option2.direction = 'Short'
option3.direction = 'Long'
#option_delta.notional = 1
option_delta.notional = option1.notional * option1.delta + option2.notional * option2.delta + option3.notional * option3.delta
option_delta.direction = 'Seller' if option_delta.notional > 0 else 'Buyer'
option_delta.notional = abs(option_delta.notional)
portf = Portfolio([option1, option2, option3, option_delta])
#Plot Scenarios Inputs: Portfolio, spread shock tightening%, spread shock widening%, snapshot period)
portf

In [ ]:
plot_trade_scenarios(portf, -.15, .8, -4, vol_time_roll=False)

In [ ]:
#Dec Jan 2017 Trade
option_delta = Index.from_tradeid(864)
option1 = BlackSwaption.from_tradeid(3, option_delta)
option2 = BlackSwaption.from_tradeid(4, option_delta)
portf = Portfolio([option1, option2, option_delta])
#plot_trade_scenarios(portf)

#Feb 2017: Sell May Buy April Calendar Trade
option_delta = Index.from_tradeid(870)
option1 = BlackSwaption.from_tradeid(5, option_delta)
option2 = BlackSwaption.from_tradeid(6, option_delta)
portf = Portfolio([option1, option2, option_delta])
#plot_trade_scenarios(portf)

#April 2017: Sell May Buy June Calendar Trade
option_delta = Index.from_tradeid(874)
option1 = BlackSwaption.from_tradeid(7, option_delta)
option2 = BlackSwaption.from_tradeid(8, option_delta)
portf = Portfolio([option1, option2, option_delta])
#plot_trade_scenarios(portf)

#June July 2017 Calendar Trade
option_delta_pf = Index.from_tradeid(874)
option_delta2_pf = Index.from_tradeid(879)

option1_pf = BlackSwaption.from_tradeid(7, option_delta_pf)
option2_pf = BlackSwaption.from_tradeid(9, option_delta_pf)
option_delta_pf.notional = 50_335_169

portf = Portfolio([option1_pf, option2_pf, option_delta_pf])
portf.value_date = datetime.date(2017, 5, 17)
portf.mark()
#plot_trade_scenarios(portf)

#July 2017: Buy Sept HY payer spread
option_delta = Index.from_tradeid(891)
option1 = BlackSwaption.from_tradeid(10, option_delta)
option2 = BlackSwaption.from_tradeid(11, option_delta)
portf = Portfolio([option1, option2, option_delta])
#plot_trade_scenarios(portf)

In [ ]:
#Look at steepness of volatility - 90 days, .75 vs .25 payer deltas
sql_str = "select b.quotedate, b.ref, b.ref_id, b.expiry, a.delta_pay, a.vol from " \
          "swaption_quotes a join swaption_ref_quotes b on a.ref_id = b.ref_id and index = 'IG'"
df = pd.read_sql_query(sql_str, dbengine('serenitasdb'), 
     index_col=['quotedate'], parse_dates={'quotedate': {'utc': True}})
df['days_expiry'] =  (df.expiry - df.index.date).dt.days
r_1 = []
for i, g in df.groupby(pd.Grouper(freq='D', level='quotedate')):
    r = []
    for i_1, g_1 in g.groupby(['days_expiry', 'delta_pay']):
        r.append([i_1[0], i_1[1], g_1['vol'].mean()])
    if len(r) > 0:
        temp = np.dstack(r)
        f = SmoothBivariateSpline(temp[0][0], temp[0][1], temp[0][2])
        r = (f(90, .75) - f(90, .25))[0][0]
        r_1.append([i, r])
    else:
        pass
df_1 = pd.DataFrame(r_1, columns=['date', 'steepness'])
df_1.set_index('date').plot()